In [21]:
import pandas as pd
import cpi
import seaborn as sns
import matplotlib.pyplot as plt
cpi.update()  

In [48]:
cpi_codes = pd.read_excel("C:\\Users\\nguye\\OneDrive\\Documents\\Python Scripts\\masterthesis\\data\\cu_item.xlsx", sheet_name="headline_cpi")

series code list: https://www.bls.gov/cpi/factsheets/cpi-series-ids.htm

In [2]:
#seasonal adjusted cpi

import pandas as pd
import json
import requests

bls_key = '0b3e11910bc54968be659b94017fabd5'

def get_bls_data(series, start, end, bls_key):
    headers = {'Content-Type': 'application/json'}
    data = json.dumps({"seriesid": series,"startyear":"%d" % (start), "endyear":"%d" % (end), "registrationKey":bls_key})
    p = requests.post('https://api.bls.gov/publicAPI/v1/timeseries/data/', data=data, headers=headers)
    json_data = json.loads(p.text)
    try:
        df = pd.DataFrame()
        for series in json_data['Results']['series']:
            df_initial = pd.DataFrame(series)
            series_col = df_initial['seriesID'][0]
            for i in range(0, len(df_initial)):
                df_row = pd.DataFrame(df_initial['data'][i])
                df_row['seriesID'] = series_col
                if 'code' not in str(df_row['footnotes']): 
                    df_row['footnotes'] = ''
                else:
                    df_row['footnotes'] = str(df_row['footnotes']).split("'code': '",1)[1][:1]
                df = df.append(df_row, ignore_index=True)
        return df
    except:
        json_data['status'] == 'REQUEST_NOT_PROCESSED'
        print('BLS API has given the following Response:', json_data['status'])
        print('Reason:', json_data['message'])


start = [2000, 2010,2020]
end = 2023


In [49]:
headline_code = cpi_codes['unadjusted'].tolist()

df = {}
for i in start:
    df[i] = get_bls_data(series=headline_code, start=i, end=end,bls_key=bls_key)


headline_cpi = pd.concat([df[2000],df[2010],df[2020]])
headline_cpi['month'] = pd.to_datetime(headline_cpi['periodName'], format="%B").dt.month
headline_cpi = headline_cpi.sort_values(['year','month']).reset_index(drop=True)
headline_cpi

C:\Users\nguye\AppData\Local\Temp\ipykernel_26100\1498945108.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\Local\Temp\ipykernel_26100\1498945108.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\Local\Temp\ipykernel_26100\1498945108.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\Local\Temp\ipykernel_26100\1498945108.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppDa

year period periodName    value footnotes         seriesID  month
0      2000    M01    January    168.8                CUUR0000SA0      1
1      2000    M01    January    126.8                CUUR0000SAA      1
2      2000    M01    January    129.2               CUUR0000SAA1      1
3      2000    M01    January    116.0               CUUR0000SAA2      1
4      2000    M01    January    146.2                CUUR0000SAC      1
...     ...    ...        ...      ...       ...              ...    ...
22081  2023    M12   December  222.337             CUUR0000SANL11     12
22082  2023    M12   December  287.273            CUUR0000SANL113     12
22083  2023    M12   December  285.811             CUUR0000SANL13     12
22084  2023    M12   December  136.811                CUUR0000SAR     12
22085  2023    M12   December   84.118               CUUR0000SARC     12

[22086 rows x 7 columns]

In [132]:
headline_df = headline_cpi.merge(cpi_codes, left_on= "seriesID", right_on="unadjusted")[['year','month','seriesID','item_name','display_level','value']]
headline_df['month'] = headline_df['year'].astype(str) + "-" + pd.to_datetime(headline_df['month'],format = "%m").dt.month.astype(str).apply(lambda i: i.zfill(2))
headline_df['value'] = headline_df['value'].apply(lambda i: round(float(i),2))

In [133]:
headline_df

year    month      seriesID               item_name  display_level  \
0      2000  2000-01   CUUR0000SA0               All items              0   
1      2000  2000-02   CUUR0000SA0               All items              0   
2      2000  2000-03   CUUR0000SA0               All items              0   
3      2000  2000-04   CUUR0000SA0               All items              0   
4      2000  2000-05   CUUR0000SA0               All items              0   
...     ...      ...           ...                     ...            ...   
22081  2023  2023-10  CUUR0000SARC  Recreation commodities              1   
22082  2023  2023-11  CUUR0000SARC  Recreation commodities              1   
22083  2023  2023-11  CUUR0000SARC  Recreation commodities              1   
22084  2023  2023-12  CUUR0000SARC  Recreation commodities              1   
22085  2023  2023-12  CUUR0000SARC  Recreation commodities              1   

        value  
0      168.80  
1      169.80  
2      171.20  
3      171.30  
4      171.50  
...       ...  
22081   85.36  
22082   84.67  
22083   84.67  
22084   84.12  
22085   84.12  

[22086 rows x 6 columns]

In [23]:
#core cpi (less food and energy)
core_cpi_series = ['CUSR0000SA0L1E']

df = {}
for i in start:
    df[i] = get_bls_data(series=core_cpi_series, start=i, end=end,bls_key=bls_key)
    
core_cpi_df = pd.concat([df[2000],df[2010],df[2020]])
core_cpi_df['month'] = pd.to_datetime(core_cpi_df['periodName'], format="%B").dt.month
core_cpi_df = core_cpi_df.sort_values(['year','month']).reset_index(drop=True)
core_cpi_df

C:\Users\nguye\AppData\Local\Temp\ipykernel_9360\3891512635.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\Local\Temp\ipykernel_9360\3891512635.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\Local\Temp\ipykernel_9360\3891512635.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\Local\Temp\ipykernel_9360\3891512635.py:26: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(df_row, ignore_index=True)
C:\Users\nguye\AppData\L

year period periodName    value footnotes        seriesID latest  month
0    2000    M01    January    179.3            CUSR0000SA0L1E    NaN      1
1    2000    M02   February    179.4            CUSR0000SA0L1E    NaN      2
2    2000    M03      March    180.0            CUSR0000SA0L1E    NaN      3
3    2000    M04      April    180.3            CUSR0000SA0L1E    NaN      4
4    2000    M05        May    180.7            CUSR0000SA0L1E    NaN      5
..    ...    ...        ...      ...       ...             ...    ...    ...
451  2023    M10    October  311.365            CUSR0000SA0L1E    NaN     10
452  2023    M11   November  312.251            CUSR0000SA0L1E    NaN     11
453  2023    M11   November  312.251            CUSR0000SA0L1E    NaN     11
454  2023    M12   December  313.216            CUSR0000SA0L1E   true     12
455  2023    M12   December  313.216            CUSR0000SA0L1E   true     12

[456 rows x 8 columns]

In [3]:
cpi_df

NameError: name 'cpi_df' is not defined